### Imports

In [1]:
# uncomment and run only to update local branch of tpg
# current local branch [June 4 2021]: new-tpg 
# pip install ../PyTPG/.

In [2]:
import numpy as np
import random
# import to do training
from tpg.trainer import Trainer
# import to run an agent (always needed)
from tpg.agent import Agent
# faster training
import multiprocessing as mp
# visual tools
from IPython.display import clear_output
import time
import matplotlib.pyplot as plt
# for writing
import csv
from datetime import date

In [3]:
def animate_path(sequence):
    current_map = np.zeros((10, 10))
    # add barrier
    for i in range(5):
        current_map[(4, i)] = 5
    # animate the run!
    for i in range(len(sequence)):
        time.sleep(0.5)
        if i == 0:
            current_map[sequence[i]] = 1
            clear_output(wait=True)
            print(0)
            print(current_map)
        else:
            current_map[sequence[i-1]] = 0
            current_map[sequence[i]] = 1
            clear_output(wait=True)
            print(i)
            print(current_map)

In [4]:
# example of above 
seq = [(0,1), (0,2), (0, 3), (1, 3), (2, 4)]
animate_path(seq)

4
[[0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 1. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [5. 5. 5. 5. 5. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]]


In [5]:
# todo: make generalizable for any GridWorld
def heat_map(sequence):
    x = [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
    y = [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
    plt.xticks(ticks=np.arange(len(x)),labels=x)
    plt.yticks(ticks=np.arange(len(y)),labels=y)
    plt.imshow(sequence, cmap='cool')

### Grid World

In [6]:
# based (for now) on Downing's Figure 4.1
class GridWorldv1:
    def __init__(self, rows, cols, win_state, starting_state): 
        self.memory = []
        self.memory_position = 0
        self.memory_limit = 20
        self.rows = rows
        self.cols = cols
        self.starting_state = starting_state
        self.win_state = win_state
        self.current_state = self.starting_state

    def sample_action (self):
        rand = random.uniform(0, 1)
        if (rand >= 0) and (rand < 0.25):
            return 0
        elif (rand >= 0.25) and (rand < 0.5):
            return 1
        elif (rand >= 0.5) and (rand < 0.75):
            return 2
        else:
            return 3
        
    def reset (self):
        self.current_state = self.starting_state
        return self.current_state
        
    def check_win (self):
        if self.current_state == self.win_state:
            return True
        return False

    # just reset for now...
    def close (self):
        self.current_state = self.starting_state
        return 1
    
    def step (self, action):
        # north
        if action == 0:
            next = (self.current_state[0] - 1, self.current_state[1])
        # south
        elif action == 1:
            next = (self.current_state[0] + 1, self.current_state[1])
        # east
        elif action == 2:
            next = (self.current_state[0], self.current_state[1] + 1)
        # west
        else:
            next = (self.current_state[0], self.current_state[1] - 1)

        terminate = False
        reward = 0
        
        # check if move is legal
        if (next[0] >= 0 and next[0] <= 9) and (next[1] >= 0 and next[1] <= 9):            
            illegal = 0
            for i in range(5):
                if next == (4, i):
                    illegal = 1
                    
            if (illegal == 0):
                self.current_state = next
                reward -= 0.01
            else:
                reward -= 1
        else:
            reward -= 1
        
        # punish repeat states within last 10 states
        if self.current_state in self.memory:
            reward -= 1
        
        if self.check_win():
            reward += 100
            terminate = True
        
        # add new state to memory
        if len(self.memory) <= self.memory_limit:
            (self.memory).append(self.current_state)
        else:
            if self.memory_position < self.memory_limit:
                self.memory[self.memory_position] = self.current_state
                self.memory_position += 1
            else:
                self.memory_position = 0
                self.memory[self.memory_position] = self.current_state
        
        return self.current_state, reward, terminate

### GridWorld Test

In [7]:
env = GridWorldv1(10, 10, (9, 0), (0, 0))
state = env.reset()
#action = agent.act(state)
action = env.sample_action()
state, reward, isDone = env.step(action)
print(state)
print(reward)
print(isDone)

(0, 0)
-1
False


### TPG Agent

In [8]:
def runAgent(args):
    agent = args[0]
    envName = args[1]
    scoreList = args[2]
    numEpisodes = args[3] # number of times to repeat game
    numFrames = args[4] 
    gen = args[5]
    
    # skip if task already done by agent
    if agent.taskDone(envName):
        print('Agent #' + str(agent.agentNum) + ' can skip.')
        scoreList.append((agent.team.id, agent.team.outcomes))
        return
    
    env = GridWorldv1(10, 10, (9, 0), (0, 0))
    valActs = 4
    
    # create environment object from above
    scoreTotal = 0
    for ep in range(numEpisodes):
        state = env.reset()
        scoreEp = 0
        states = []
        step_map = np.zeros((10, 10))
        if numEpisodes > 1:
            for i in range(numFrames): # frame loop           
                # action selection
                act = agent.act(state)
                
                state, reward, isDone = env.step(act)
                # for heatmap
                step_map[state] = step_map[state] + 1
                states.append(state)
                #print('State: ' + str(state))
                scoreEp += reward
                
                # win
                if isDone:
                    print('win!')
                    print(states)
                    break
                    
            print('Agent #' + str(agent.agentNum) + 
              ' | Ep #' + str(ep) + ' | Score: ' + str(scoreEp))
            
        scoreTotal += scoreEp
    scoreTotal /= numEpisodes
    env.close()
    agent.reward(scoreTotal, envName)
    scoreList.append((agent.team.id, agent.team.outcomes))
    if isDone:
        return states
    else:
        return 0

### All Together Now!

In [ ]:
# NOTES:
# pAtomic equal to 1 so teams are single nodes
    # starting off, teams don't reference teams
# if the maxTeamSize is set, we can try to maximize the use of actually useful learners.
    # this might help with the consistency of success...
filename = 'results/' + str(date.today()) + '.csv'
for trial in range(5):
    trainer = Trainer(actions=4, teamPopSize=50, pActAtom=1.0, 
                      nRegisters=4, initMaxActProgSize=48, gap=0.5)

    envName = 'GridWorldv1'
    allScores = []
    champions = []
    for gen in range(500):
        scoreList = []

        agents = trainer.getAgents()

        agent_track = 0
        best_score = -200.0
        curr_champion = []
        for agent in agents:
            run = runAgent([agent, envName, scoreList, 10, 100, gen])
            if (scoreList[agent_track][1]['GridWorldv1'] > best_score) and (run != 0):
                best_score = scoreList[agent_track][1]['GridWorldv1']
                curr_champion = run
                print(run)
            agent_track += 1
        
        champions.append(curr_champion)
        
        # apply scores, must do this when multiprocessing
        # because agents can't refer to trainer
        teams = trainer.applyScores(scoreList)

        trainer.evolve(tasks=[envName]) # go into next gen

        # an easier way to track stats than the above example
        scoreStats = trainer.fitnessStats

        allScores.append((scoreStats['min'], scoreStats['max'], scoreStats['average']))

        print('Gen: ' + str(gen))
        print('Results so far: ' + str(allScores))

    print('Results:\nMin, Max, Avg')
    for score in allScores:
        print(score[0],score[1],score[2])
    
    with open(filename, 'w') as csvfile: 
        csvwriter = csv.writer(csvfile)
        csvwriter.writerow([trial])
        for champion in champions:
            if champion != None:
                csvwriter.writerow(champion)
        y = []
        for score in allScores:
            y.append(score[1])
        csvwriter.writerow(y)

Agent #0 | Ep #0 | Score: -199
Agent #0 | Ep #1 | Score: -200
Agent #0 | Ep #2 | Score: -200
Agent #0 | Ep #3 | Score: -200
Agent #0 | Ep #4 | Score: -200
Agent #0 | Ep #5 | Score: -200
Agent #0 | Ep #6 | Score: -200
Agent #0 | Ep #7 | Score: -200
Agent #0 | Ep #8 | Score: -200
Agent #0 | Ep #9 | Score: -200
Agent #1 | Ep #0 | Score: -198.01
Agent #1 | Ep #1 | Score: -199
Agent #1 | Ep #2 | Score: -200
Agent #1 | Ep #3 | Score: -200
Agent #1 | Ep #4 | Score: -200
Agent #1 | Ep #5 | Score: -200
Agent #1 | Ep #6 | Score: -200
Agent #1 | Ep #7 | Score: -200
Agent #1 | Ep #8 | Score: -200
Agent #1 | Ep #9 | Score: -200
Agent #2 | Ep #0 | Score: -199
Agent #2 | Ep #1 | Score: -200
Agent #2 | Ep #2 | Score: -200
Agent #2 | Ep #3 | Score: -200
Agent #2 | Ep #4 | Score: -200
Agent #2 | Ep #5 | Score: -200
Agent #2 | Ep #6 | Score: -200
Agent #2 | Ep #7 | Score: -200
Agent #2 | Ep #8 | Score: -200
Agent #2 | Ep #9 | Score: -200
Agent #3 | Ep #0 | Score: -199
Agent #3 | Ep #1 | Score: -200
Agent

Agent #32 | Ep #3 | Score: -164.18
Agent #32 | Ep #4 | Score: -164.18
Agent #32 | Ep #5 | Score: -164.18
Agent #32 | Ep #6 | Score: -164.18
Agent #32 | Ep #7 | Score: -164.18
Agent #32 | Ep #8 | Score: -164.18
Agent #32 | Ep #9 | Score: -164.18
Agent #33 | Ep #0 | Score: -196.01999999999998
Agent #33 | Ep #1 | Score: -200
Agent #33 | Ep #2 | Score: -200
Agent #33 | Ep #3 | Score: -200
Agent #33 | Ep #4 | Score: -200
Agent #33 | Ep #5 | Score: -182.09000000000003
Agent #33 | Ep #6 | Score: -183.09
Agent #33 | Ep #7 | Score: -183.09
Agent #33 | Ep #8 | Score: -183.09
Agent #33 | Ep #9 | Score: -183.09
Agent #34 | Ep #0 | Score: -198.01
Agent #34 | Ep #1 | Score: -199
Agent #34 | Ep #2 | Score: -200
Agent #34 | Ep #3 | Score: -200
Agent #34 | Ep #4 | Score: -199.01
Agent #34 | Ep #5 | Score: -199
Agent #34 | Ep #6 | Score: -200
Agent #34 | Ep #7 | Score: -200
Agent #34 | Ep #8 | Score: -199.01
Agent #34 | Ep #9 | Score: -199
Agent #35 | Ep #0 | Score: -199
Agent #35 | Ep #1 | Score: -200


Agent #30 | Ep #1 | Score: -195.03
Agent #30 | Ep #2 | Score: -195.03
Agent #30 | Ep #3 | Score: -195.03
Agent #30 | Ep #4 | Score: -195.03
Agent #30 | Ep #5 | Score: -195.03
Agent #30 | Ep #6 | Score: -195.03
Agent #30 | Ep #7 | Score: -195.03
Agent #30 | Ep #8 | Score: -195.03
Agent #30 | Ep #9 | Score: -195.03
Agent #31 | Ep #0 | Score: -199
Agent #31 | Ep #1 | Score: -200
Agent #31 | Ep #2 | Score: -200
Agent #31 | Ep #3 | Score: -200
Agent #31 | Ep #4 | Score: -200
Agent #31 | Ep #5 | Score: -200
Agent #31 | Ep #6 | Score: -200
Agent #31 | Ep #7 | Score: -200
Agent #31 | Ep #8 | Score: -200
Agent #31 | Ep #9 | Score: -200
Agent #32 | Ep #0 | Score: -148.50000000000006
Agent #32 | Ep #1 | Score: -150.50000000000003
Agent #32 | Ep #2 | Score: -150.50000000000003
Agent #32 | Ep #3 | Score: -150.50000000000003
Agent #32 | Ep #4 | Score: -150.50000000000003
Agent #32 | Ep #5 | Score: -150.50000000000003
Agent #32 | Ep #6 | Score: -150.50000000000003
Agent #32 | Ep #7 | Score: -150.5000

Agent #30 | Ep #2 | Score: -183.09
Agent #30 | Ep #3 | Score: -183.09
Agent #30 | Ep #4 | Score: -183.09
Agent #30 | Ep #5 | Score: -183.09
Agent #30 | Ep #6 | Score: -183.09
Agent #30 | Ep #7 | Score: -183.09
Agent #30 | Ep #8 | Score: -183.09
Agent #30 | Ep #9 | Score: -183.09
Agent #31 | Ep #0 | Score: -145.51000000000005
Agent #31 | Ep #1 | Score: -147.51000000000005
Agent #31 | Ep #2 | Score: -167.31000000000003
Agent #31 | Ep #3 | Score: -195.03
Agent #31 | Ep #4 | Score: -195.03
Agent #31 | Ep #5 | Score: -195.03
Agent #31 | Ep #6 | Score: -195.03
Agent #31 | Ep #7 | Score: -195.03
Agent #31 | Ep #8 | Score: -195.03
Agent #31 | Ep #9 | Score: -161.37
Agent #32 | Ep #0 | Score: -147.51000000000002
Agent #32 | Ep #1 | Score: -150.50000000000003
Agent #32 | Ep #2 | Score: -150.50000000000003
Agent #32 | Ep #3 | Score: -150.50000000000003
Agent #32 | Ep #4 | Score: -150.50000000000003
Agent #32 | Ep #5 | Score: -150.50000000000003
Agent #32 | Ep #6 | Score: -150.50000000000003
Agent

Agent #29 | Ep #7 | Score: -200
Agent #29 | Ep #8 | Score: -200
Agent #29 | Ep #9 | Score: -200
Agent #30 | Ep #0 | Score: -199
Agent #30 | Ep #1 | Score: -200
Agent #30 | Ep #2 | Score: -200
Agent #30 | Ep #3 | Score: -200
Agent #30 | Ep #4 | Score: -200
Agent #30 | Ep #5 | Score: -200
Agent #30 | Ep #6 | Score: -200
Agent #30 | Ep #7 | Score: -200
Agent #30 | Ep #8 | Score: -200
Agent #30 | Ep #9 | Score: -200
Agent #31 | Ep #0 | Score: -182.09
Agent #31 | Ep #1 | Score: -183.09
Agent #31 | Ep #2 | Score: -183.09
Agent #31 | Ep #3 | Score: -183.09
Agent #31 | Ep #4 | Score: -183.09
Agent #31 | Ep #5 | Score: -183.09
Agent #31 | Ep #6 | Score: -183.09
Agent #31 | Ep #7 | Score: -183.09
Agent #31 | Ep #8 | Score: -183.09
Agent #31 | Ep #9 | Score: -183.09
Agent #32 | Ep #0 | Score: -199
Agent #32 | Ep #1 | Score: -200
Agent #32 | Ep #2 | Score: -200
Agent #32 | Ep #3 | Score: -200
Agent #32 | Ep #4 | Score: -200
Agent #32 | Ep #5 | Score: -200
Agent #32 | Ep #6 | Score: -200
Agent #32 

...

Agent #48 | Ep #8 | Score: -101.00000000000014
Agent #48 | Ep #9 | Score: -101.00000000000014
Agent #49 | Ep #0 | Score: -164.18
Agent #49 | Ep #1 | Score: -165.18
Agent #49 | Ep #2 | Score: -165.18
Agent #49 | Ep #3 | Score: -166.18
Agent #49 | Ep #4 | Score: -166.18
Agent #49 | Ep #5 | Score: -165.18
Agent #49 | Ep #6 | Score: -166.18
Agent #49 | Ep #7 | Score: -166.18
Agent #49 | Ep #8 | Score: -165.18
Agent #49 | Ep #9 | Score: -166.18
Gen: 226
Results so far: [(-199.9, -109.70600000000013, -193.9276399999999), (-199.9, -100.80000000000013, -186.22114000000002), (-199.9, -100.80000000000013, -180.14102), (-199.9, -100.80000000000013, -178.49407999999985), (-199.9, -100.80000000000013, -171.20739999999995), (-199.9, -100.80000000000013, -162.07332), (-199.9, -100.80000000000013, -154.51306000000002), (-199.9, -100.80000000000013, -153.53974000000005), (-199.9, -100.80000000000013, -150.56516000000002), (-199.9, -100.80000000000013, -152.12901999999997), (-199.9, -100.80000000000013,

Agent #27 | Ep #7 | Score: -195.03
Agent #27 | Ep #8 | Score: -195.03
Agent #27 | Ep #9 | Score: -195.03
Agent #28 | Ep #0 | Score: -99.00000000000014
Agent #28 | Ep #1 | Score: -101.00000000000014
Agent #28 | Ep #2 | Score: -101.00000000000014
Agent #28 | Ep #3 | Score: -101.00000000000014
Agent #28 | Ep #4 | Score: -101.00000000000014
Agent #28 | Ep #5 | Score: -101.00000000000014
Agent #28 | Ep #6 | Score: -101.00000000000014
Agent #28 | Ep #7 | Score: -101.00000000000014
Agent #28 | Ep #8 | Score: -101.00000000000014
Agent #28 | Ep #9 | Score: -101.00000000000014
Agent #29 | Ep #0 | Score: -199
Agent #29 | Ep #1 | Score: -200
Agent #29 | Ep #2 | Score: -200
Agent #29 | Ep #3 | Score: -200
Agent #29 | Ep #4 | Score: -200
Agent #29 | Ep #5 | Score: -200
Agent #29 | Ep #6 | Score: -200
Agent #29 | Ep #7 | Score: -200
Agent #29 | Ep #8 | Score: -200
Agent #29 | Ep #9 | Score: -200
Agent #30 | Ep #0 | Score: -99.00000000000014
Agent #30 | Ep #1 | Score: -101.00000000000014
Agent #30 | E

Agent #48 | Ep #2 | Score: -188.09
Agent #48 | Ep #3 | Score: -183.09
Agent #48 | Ep #4 | Score: -183.09
Agent #48 | Ep #5 | Score: -183.09
Agent #48 | Ep #6 | Score: -183.09
Agent #48 | Ep #7 | Score: -183.09
Agent #48 | Ep #8 | Score: -183.09
Agent #48 | Ep #9 | Score: -183.09
Agent #49 | Ep #0 | Score: -182.09
Agent #49 | Ep #1 | Score: -183.09
Agent #49 | Ep #2 | Score: -183.09
Agent #49 | Ep #3 | Score: -183.09
Agent #49 | Ep #4 | Score: -183.09
Agent #49 | Ep #5 | Score: -183.09
Agent #49 | Ep #6 | Score: -183.09
Agent #49 | Ep #7 | Score: -183.09
Agent #49 | Ep #8 | Score: -183.09
Agent #49 | Ep #9 | Score: -183.09
Gen: 227
Results so far: [(-199.9, -109.70600000000013, -193.9276399999999), (-199.9, -100.80000000000013, -186.22114000000002), (-199.9, -100.80000000000013, -180.14102), (-199.9, -100.80000000000013, -178.49407999999985), (-199.9, -100.80000000000013, -171.20739999999995), (-199.9, -100.80000000000013, -162.07332), (-199.9, -100.80000000000013, -154.51306000000002),

Agent #27 | Ep #5 | Score: -101.00000000000014
Agent #27 | Ep #6 | Score: -101.00000000000014
Agent #27 | Ep #7 | Score: -101.00000000000014
Agent #27 | Ep #8 | Score: -101.00000000000014
Agent #27 | Ep #9 | Score: -101.00000000000014
Agent #28 | Ep #0 | Score: -196.01999999999998
Agent #28 | Ep #1 | Score: -200
Agent #28 | Ep #2 | Score: -200
Agent #28 | Ep #3 | Score: -170.28999999999974
Agent #28 | Ep #4 | Score: -101.99000000000015
Agent #28 | Ep #5 | Score: -101.99000000000015
Agent #28 | Ep #6 | Score: -101.99000000000015
Agent #28 | Ep #7 | Score: -101.99000000000015
Agent #28 | Ep #8 | Score: -101.99000000000015
Agent #28 | Ep #9 | Score: -101.99000000000015
Agent #29 | Ep #0 | Score: -182.09
Agent #29 | Ep #1 | Score: -183.09
Agent #29 | Ep #2 | Score: -183.09
Agent #29 | Ep #3 | Score: -183.09
Agent #29 | Ep #4 | Score: -183.09
Agent #29 | Ep #5 | Score: -183.09
Agent #29 | Ep #6 | Score: -183.09
Agent #29 | Ep #7 | Score: -183.09
Agent #29 | Ep #8 | Score: -183.09
Agent #29 

Agent #25 | Ep #8 | Score: -101.00000000000014
Agent #25 | Ep #9 | Score: -101.00000000000014
Agent #26 | Ep #0 | Score: -99.99000000000014
Agent #26 | Ep #1 | Score: -99.00000000000014
Agent #26 | Ep #2 | Score: -101.00000000000014
Agent #26 | Ep #3 | Score: -141.56999999999996
Agent #26 | Ep #4 | Score: -195.03
Agent #26 | Ep #5 | Score: -195.03
Agent #26 | Ep #6 | Score: -195.03
Agent #26 | Ep #7 | Score: -195.03
Agent #26 | Ep #8 | Score: -195.03
Agent #26 | Ep #9 | Score: -195.03
Agent #27 | Ep #0 | Score: -99.00000000000014
Agent #27 | Ep #1 | Score: -101.00000000000014
Agent #27 | Ep #2 | Score: -101.00000000000014
Agent #27 | Ep #3 | Score: -101.00000000000014
Agent #27 | Ep #4 | Score: -101.00000000000014
Agent #27 | Ep #5 | Score: -101.00000000000014
Agent #27 | Ep #6 | Score: -101.00000000000014
Agent #27 | Ep #7 | Score: -101.00000000000014
Agent #27 | Ep #8 | Score: -101.00000000000014
Agent #27 | Ep #9 | Score: -101.00000000000014
Agent #28 | Ep #0 | Score: -196.019999999

In [ ]:
x = []
y = []
for i in range(500):
    x.append(i)
for score in allScores:
    y.append(score[1])
plt.xlabel('Generation')
plt.ylabel('Max Score')
plt.plot(x, y)
plt.show()

In [ ]:
x = []
y = []
for i in range(500):
    x.append(i)

for score in allScores:
    y.append(score[2])
plt.xlabel('Generation')
plt.ylabel('Average Score')
plt.plot(x, y)
plt.show()